In [262]:
import agentpy as ap
import numpy as np
import matplotlib.pyplot as plt
import math
import IPython
import json
import random

In [263]:
myJson={
    "carsAmount": 0,
    "steps":[]
}

def convertToJson():
    with open("variables.json", "w") as outfile:
        json.dump(myJson, outfile)

class Semaphore(ap.Agent):
    def setup(self):
        self.step_time = 0.1
        self.direction = [0, 1]
        self.state = 0 # green = 0, yellow = 1, red = 2
        self.state_time = 0

        self.state_time_total = 0

        self.green_duration = 50
        self.yellow_duration = 5
        self.red_duration = 45

    def update(self) :
        self.state_time += self.step_time

        if self.state == 0:
            self.state_time_total += self.step_time
            if self.state_time >= self.green_duration:
                self.state = 1
                self.state_time = 0

        if self.state == 1:
            if self.state_time >= self.yellow_duration:
                self.state = 2
                self.state_time = 0

        if self.state == 2:
            if self.state_time >= self.red_duration:
                self.state = 0
                self.state_time = 0

    def set_green(self):
        self.state = 0
        self.state_time = 0
    
    def set_yellow(self):
        self.state = 1
        self.state_time = 0

    def set_red(self):
        self.state = 2
        self.state_time = 0

In [264]:
class Car(ap.Agent):
    def setup(self):
        self.step_time = 0.1
        self.direction = [0, 1]
        self.speed = 0.0
        self.max_speed = 16.66
        self.state = 1 # 0 = chocado, 1 = ok

    def update_position(self):
        if self.state == 0:
            return
        
        # Posibilidad de dar vuelta

        # Vuelta hacia east
        if self.model.avenue.positions[self][1] > self.p.size//2-20 and self.model.avenue.positions[self][1] < self.p.size//2+0.1 and self.direction == [0,1]:
            print(self.model.avenue.positions[self])
            if random.randint(1, 6) == 1:
                self.direction = [1,0]
                self.model.avenue.move_to(self, [self.model.avenue.positions[self][0], self.p.size//2-20])
        
        # Vuelta hacia west
        elif self.model.avenue.positions[self][1] < self.p.size//2 and self.model.avenue.positions[self][1] > self.p.size//2-0.1 and self.direction == [0,-1]:
            if random.randint(1, 6) == 1:
                self.direction = [-1,0]
                self.model.avenue.move_to(self, [self.model.avenue.positions[self][0], self.p.size//2])
        
        # Vuelta hacia south
        elif self.model.avenue.positions[self][0] > self.p.size//2-20 and self.model.avenue.positions[self][0] < self.p.size//2+0.1 and self.direction == [1,0]:
            if random.randint(1, 6) == 1:
                self.direction = [0,-1]
                self.model.avenue.move_to(self, [self.p.size//2-20, self.model.avenue.positions[self][1]])
        
        # Vuelta hacia north
        elif self.model.avenue.positions[self][0] < self.p.size//2 and self.model.avenue.positions[self][0] > self.p.size//2-0.1 and self.direction == [-1,0]:
            if random.randint(1, 6) == 1:
                self.direction = [0,1]
                self.model.avenue.move_to(self, [self.p.size//2, self.model.avenue.positions[self][1]])

        
        self.model.avenue.move_by(self, [self.speed*self.step_time*self.direction[0], self.speed*self.step_time*self.direction[1]])

    def update_speed(self):
        if self.state == 0:
            return
        
        p = self.model.avenue.positions[self]

        min_car_distance = 10000000
        for car in self.model.cars:
            if car == self:
                continue

            dot_p1 = self.direction[0]*car.direction[0] + self.direction[1]*car.direction[1]

            p2 = self.model.avenue.positions[car]
            dot_p2 = (p2[0] - p[0])*self.direction[0] + (p2[1] - p[1])*self.direction[1]

            if dot_p1 > 0 and dot_p2 > 0:
                d = math.sqrt((p2[0] - p[0])**2 + (p2[1] - p[1])**2)
                if d < min_car_distance:
                    min_car_distance = d

        min_semaphore_distance = 10000000
        semaphore_state = 0
        for semaphore in self.model.semaphores:

            dot_p1 = self.direction[0]*semaphore.direction[0] + self.direction[1]*semaphore.direction[1]

            p2 = self.model.avenue.positions[semaphore]
            dot_p2 = (p2[0] - p[0])*self.direction[0] + (p2[1] - p[1])*self.direction[1]

            if dot_p1 < 0 and dot_p2 > 0:
                d = math.sqrt((p2[0] - p[0])**2 + (p2[1] - p[1])**2)
                if d < min_semaphore_distance:
                    min_semaphore_distance = d
                    semaphore_state = semaphore.state
                
        if min_car_distance < 2:
            self.speed = 0
            self.state = 1

        elif min_car_distance < 10:
            self.speed = np.maximum(self.speed - 50*self.step_time, 0)
        
        elif min_car_distance < 15:
            self.speed = np.maximum(self.speed - 50*self.step_time, 0)
        
        elif min_semaphore_distance < 20 and semaphore_state == 1:
            self.speed = np.minimum(self.speed + 2.5*self.step_time, self.max_speed)

        elif min_semaphore_distance < 40 and semaphore_state == 1:
            self.speed = np.maximum(self.speed - 2.5*self.step_time, 5)

        elif min_semaphore_distance < 30 and semaphore_state == 2:
            self.speed = np.maximum(self.speed - 10*self.step_time, 0)

        elif min_semaphore_distance < 50 and semaphore_state == 2:
            self.speed = np.maximum(self.speed - 2.5*self.step_time, 5)

        else:
            self.speed = np.minimum(self.speed + 2.0*self.step_time, self.max_speed)

In [265]:
stepCount=0
class AvenueModel(ap.Model):
    def setup(self):

        myJson["carsAmount"] = self.p.cars

        self.cars = ap.AgentList(self, self.p.cars, Car)
        self.cars.step_time = self.p.step_time
        self.cars.speed = self.p.v0
        self.stepCount=0

        c_north = self.p.cars//4
        c_south = self.p.cars//4
        c_east = self.p.cars//4
        c_west = self.p.cars - c_north - c_south - c_east

        for k in range(c_north):
            self.cars[k].direction = [0, 1]

        for k in range(c_south):
            self.cars[c_north + k].direction = [0, -1]
        
        # Direccion a carros este y oeste

        for k in range(c_east):
            self.cars[c_north + c_south + k].direction = [1, 0]
        
        for k in range(c_west):
            self.cars[c_north + c_south + c_east + k].direction = [-1, 0]
        
        self.semaphores = ap.AgentList(self, 4, Semaphore)
        self.semaphores.step_time = self.p.step_time
        self.semaphores.green_duration = self.p.green
        self.semaphores.yellow_duration = self.p.yellow
        self.semaphores.red_duration = self.p.red
        self.semaphores[0].direction = [0, 1]
        self.semaphores[1].direction = [0, -1]
        self.semaphores[2].direction = [1, 0]
        self.semaphores[3].direction = [-1, 0]

        self.avenue = ap.Space(self, shape = [self.p.size, self.p.size], torus = True)

        self.avenue.add_agents(self.semaphores, random=True)
        self.avenue.move_to(self.semaphores[0], [self.p.size//2-30, self.p.size//2+60])
        self.avenue.move_to(self.semaphores[1], [self.p.size//2+10, self.p.size//2-60])


        self.avenue.move_to(self.semaphores[2], [self.p.size//2+60, self.p.size//2+10])
        self.avenue.move_to(self.semaphores[3], [self.p.size//2-60, self.p.size//2-30])
        self.semaphores[2].state = 2
        self.semaphores[3].state = 2

        self.avenue.add_agents(self.cars, random=True)

        # Acomodar carros
        for k in range(c_north):
            self.avenue.move_to(self.cars[k], [self.p.size//2, 10*(k+1)])

        for k in range(c_south):
            self.avenue.move_to(self.cars[k+c_north], [self.p.size//2-20, self.p.size - 10*(k+1)])

        for k in range(c_east):
            self.avenue.move_to(self.cars[k+c_north+c_south], [10*(k+1), self.p.size//2-20])
        
        for k in range(c_west):
            self.avenue.move_to(self.cars[k+c_north+c_south+c_east], [self.p.size - 10*(k+1), self.p.size//2])
        
        #Usamos la info para generar el JSON
        cars=[]
        semaphores=[]
        
        for c in range(len(self.cars)):
            currentInfo={
                "id":self.cars[c].id,
                "x":self.model.avenue.positions[self.cars[c]][0],
                "z":self.model.avenue.positions[self.cars[c]][1],
                "y":self.p.y,
                "direction":self.cars[c].direction
            }
            cars.append(currentInfo)
        
        for s in range(len(self.semaphores)):
            currentInfo={
                "x":self.model.avenue.positions[self.semaphores[s]][0],
                "z":self.model.avenue.positions[self.semaphores[s]][1],
                "y":self.p.y,
                "direction":self.semaphores[s].direction,
                "state":self.semaphores[s].state,
                
            }
            semaphores.append(currentInfo)
        
        myJson["steps"].append({
            "id":self.stepCount,
            "cars":cars,
            "semaphores":semaphores
        })
 
    def step(self):
        self.stepCount+=1

        self.semaphores.update()

        self.cars.update_position()
        self.cars.update_speed()
        
        #Usamos la info para generar el JSON
        cars=[]
        semaphores=[]
        for c in range(len(self.cars)):
            currentInfo={
                "id":self.cars[c].id,
                "x":self.model.avenue.positions[self.cars[c]][0],
                "z":self.model.avenue.positions[self.cars[c]][1],
                "y":self.p.y,
                "direction":self.cars[c].direction
            }
            cars.append(currentInfo)
        
        for s in range(len(self.semaphores)):
            currentInfo={
                "x":self.model.avenue.positions[self.semaphores[s]][0],
                "z":self.model.avenue.positions[self.semaphores[s]][1],
                "y":self.p.y,
                "direction":self.semaphores[s].direction,
                "state":self.semaphores[s].state,
                
            }
            semaphores.append(currentInfo)
        
        myJson["steps"].append({
            "id":self.stepCount,
            "cars":cars,
            "semaphores":semaphores
        })
        
    def update(self):
        crashes = len(self.cars.select(self.cars.state == 0))
        self.record('Colisiones', crashes)
    
    def end(self):
        crashes = len(self.cars.select(self.cars.state == 0))
        self.report('Colisiones', crashes)
        convertToJson()

In [266]:
parameters = {
    'steps': 500,
    'step_time': 0.1,
    'size': 500,
    'green': 15,
    'yellow': 5,
    'red': 20,
    'cars': 20,
    'v0': 0,
    'y':0
}

In [267]:
def animation_plot_single(m, ax):
    ax.set_title(f"Avenida t={m.t*m.p.step_time:.2f}")

    colors = ["green", "yellow", "red"]

    pos_s1 = m.avenue.positions[m.semaphores[0]]
    ax.scatter(*pos_s1, s=20, c=colors[m.semaphores[0].state])

    pos_s2 = m.avenue.positions[m.semaphores[1]]
    ax.scatter(*pos_s2, s=20, c=colors[m.semaphores[1].state])
    
    pos_s3 = m.avenue.positions[m.semaphores[2]]
    ax.scatter(*pos_s3, s=20, c=colors[m.semaphores[2].state])
    
    pos_s4 = m.avenue.positions[m.semaphores[3]]
    ax.scatter(*pos_s4, s=20, c=colors[m.semaphores[3].state])

    ax.set_xlim(0, m.avenue.shape[0])
    ax.set_ylim(0, m.avenue.shape[1])
    
    count = 0

    for car in m.cars:
        pos_c = m.avenue.positions[car]
        if count < m.p.cars//2:
            ax.scatter(*pos_c, s=20, c="black")
        else:
            ax.scatter(*pos_c, s=20, c="blue")
        count += 1

    ax.set_axis_off()
    ax.set_aspect('equal', 'box')

def animation_plot(m, p):
    fig = plt.figure(figsize=(10, 10))
    ax = fig.add_subplot(111)
    animation = ap.animate(m(p), fig, ax, animation_plot_single)
    return IPython.display.HTML(animation.to_jshtml(fps=20))

In [268]:
model = AvenueModel(parameters)
results = model.run()

Completed: 151 steps[250.    231.342]
Completed: 152 steps[250.    233.008]
Completed: 153 steps[250.    234.674]
Completed: 154 steps[250.   236.34]
Completed: 155 steps[250.    238.006]
Completed: 156 steps[250.    239.672]
Completed: 157 steps[250.    241.338]
Completed: 158 steps[250.    243.004]
Completed: 159 steps[250.   244.67]
Completed: 160 steps[250.    246.336]
Completed: 161 steps[250.    248.002]
Completed: 162 steps[250.    249.668]
Completed: 179 steps[250.    231.338]
Completed: 180 steps[250.    233.004]
Completed: 181 steps[250.   234.67]
Completed: 182 steps[250.    236.336]
Completed: 183 steps[250.    238.002]
Completed: 184 steps[250.    239.668]
Completed: 185 steps[250.    241.334]
Completed: 186 steps[250. 243.]
Completed: 187 steps[250.    244.666]
Completed: 188 steps[250.    246.332]
Completed: 189 steps[250.    247.998]
Completed: 190 steps[250.    249.664]
Completed: 210 steps[250.    230.677]
Completed: 211 steps[250.    232.343]
Completed: 212 steps[250

In [269]:
# Autos colisionados en cada iteración
results.variables.AvenueModel

Colisiones
t              
0             0
1             0
2             0
3             0
4             0
..          ...
496           0
497           0
498           0
499           0
500           0

[501 rows x 1 columns]

In [270]:
# Información al final de la simulación
results.reporters

seed  Colisiones
0  155483593319480744195502724289341216636           0

In [271]:
animation_plot(AvenueModel, parameters)

[250.    231.342]
[250.    231.338]
[250.    233.004]
[250.   234.67]
[250.    230.677]
[250.    232.343]
[250.    234.009]
[250.    235.675]
[250.    237.341]
[250.    239.007]
[250.    240.673]
[250.    242.339]
[250.    244.005]
[250.    245.671]
[250.    230.744]
[250.    231.541]
[250.    233.161]
[250.    234.801]
